In [1]:

# by Todd Arbetter (todd.e.arbetter@gmail.com)


#Load a bunch of modules

import numpy as np
import pandas as pd
import geopandas as gpd
import streamlit as st
import folium as fl
from folium.plugins import FastMarkerCluster,MarkerCluster,MiniMap,HeatMap
from folium.features import DivIcon
import streamlit_folium as sf
import branca.colormap as cm
import os as os
#import wget
import tarfile
import datetime as dt
import matplotlib.pyplot as plt
#import Iframe
import base64
import re

print('loaded 9 modules')

loaded 9 modules


In [2]:
 #Make sure we're in the correct direcotyr

os.chdir('/Users/arbetter/Coding/Streamlit/IXWater-Suncor')

In [3]:
pd.options.display.max_columns=None
pd.options.display.max_rows=None

In [4]:
outfalls_df = pd.read_csv('Outfalls_for Map_22Nov212.csv')

#strip trailing whitespace from column header
for column in outfalls_df.columns:
    col = column.strip()
    outfalls_df.rename(columns={column:col},inplace=True)
    print(column,col)
    
outfalls_df.head()

Outfall  Outfall
Description  Description
Latitude  Latitude
Longitude  Longitude
Wastewater Source  Wastewater Source
Receiving Water  Receiving Water


Outfall                                        Description  \
0             002B                               Internal outfall 002    
1             003B                               Internal outfall 003    
2             020A   External outfall 020A (at outfall on Sand Creek)    
3  020Z (for PFAS)   External outfall 020A (at outfall on Sand Creek)    
4             004A   Mary’s Pond – Plant 3 (northwest corner outfall)    

    Latitude     Longitude                                  Wastewater Source  \
0   39.8050     -104.9494   Petroleum refining and related operations, gro...   
1   39.8072     -104.9475                            Groundwater remediation    
2  39.80853     -104.9476   Combination of treated wastewater from Outfall...   
3  39.80853     -104.9476   Combination of treated wastewater from Outfall...   
4   39.8075   -104.946667   Stormwater runoff from Plant 3 (asphalt plant)...   

                     Receiving Water  
0             NA (see Outfall 020A)   
1             NA (see Outfall 020A)   
2  Sand Creek to South Platte River   
3  Sand Creek to South Platte River   
4  Sand Creek to South Platte River

In [5]:
outfalls_gdf = gpd.GeoDataFrame(outfalls_df,geometry=gpd.points_from_xy(outfalls_df.Longitude,outfalls_df.Latitude))

outfalls_gdf.set_crs('EPSG:4269',inplace=True)

### Maybe separate the PFAS Z outfall from the A and B outfall, get the tooltip to show one on the left side and the other
##on the right side of the circle marker

Outfall                                        Description  \
0              002B                               Internal outfall 002    
1              003B                               Internal outfall 003    
2              020A   External outfall 020A (at outfall on Sand Creek)    
3   020Z (for PFAS)   External outfall 020A (at outfall on Sand Creek)    
4              004A   Mary’s Pond – Plant 3 (northwest corner outfall)    
5   004Z (for PFAS)   Mary’s Pond – Plant 3 (northwest corner outfall)    
6              021A         Nelson Property (northeast corner outfall)    
7   021Z (for PFAS)         Nelson Property (northeast corner outfall)    
8              022A       Nelson Property pond (northwest corner pond)    
9   022Z (for PFAS)       Nelson Property pond (northwest corner pond)    
10             023A       Detention area – Plant 1 (west end of swale)    
11  023Z (for PFAS)       Detention area – Plant 1 (west end of swale)    
12             024A               Detention area – Plant 2 (north end)    
13  024Z (for PFAS)               Detention area – Plant 2 (north end)    
14             025A   High flow outfall – Plant 1 (at sulfur rail lo...   
15  025Z (for PFAS)   High flow outfall – Plant 1 (at sulfur rail lo...   
16             026A   High flow outfall – Plant 3 (at ditch inlet to...   
17  026Z (for PFAS)   High flow outfall – Plant 3 (at ditch inlet to...   
18             027A                   Accumulated Stormwater – Plant 2    
19  027Z (for PFAS)                   Accumulated Stormwater – Plant 2    
20             028A   Retention pond – Plant 2 (southwest corner of ...   
21  028Z (for PFAS)   Retention pond – Plant 2 (southwest corner of ...   

      Latitude     Longitude  \
0     39.8050     -104.9494    
1     39.8072     -104.9475    
2    39.80853     -104.9476    
3    39.80853     -104.9476    
4     39.8075   -104.946667    
5     39.8075   -104.946667    
6   39.810278   -104.940556    
7   39.810278   -104.940556    
8   39.810318   -104.943202    
9   39.810318   -104.943202    
10  39.809017    -104.94901    
11  39.809017    -104.94901    
12  39.804822   -104.942079    
13  39.804822   -104.942079    
14  39.804025   -104.944022    
15  39.804025   -104.944022    
16   39.80376   -104.940982    
17   39.80376   -104.940982    
18   39.801156   -104.94437    
19   39.801156   -104.94437    
20   39.796733   -104.95148    
21   39.796733   -104.95148    

                                    Wastewater Source  \
0   Petroleum refining and related operations, gro...   
1                            Groundwater remediation    
2   Combination of treated wastewater from Outfall...   
3   Combination of treated wastewater from Outfall...   
4   Stormwater runoff from Plant 3 (asphalt plant)...   
5   Stormwater runoff from Plant 3 (asphalt plant)...   
6   Stormwater runoff from Suncor maintenance faci...   
7   Stormwater runoff from Suncor maintenance faci...   
8   Stormwater runoff from Suncor maintenance faci...   
9   Stormwater runoff from Suncor maintenance faci...   
10  Stormwater runoff from Suncor Plant 1 (SWA Nos...   
11  Stormwater runoff from Suncor Plant 1 (SWA Nos...   
12  Stormwater runoff from Suncor Plant 2 (SWA No....   
13  Stormwater runoff from Suncor Plant 2 (SWA No....   
14  Stormwater runoff from Suncor Plant 1 (SWA No....   
15  Stormwater runoff from Suncor Plant 1 (SWA No....   
16  Stormwater runoff from Suncor Plant 3 commingl...   
17  Stormwater runoff from Suncor Plant 3 commingl...   
18  Accumulated stormwater runoff from East Tank F...   
19  Accumulated stormwater runoff from East Tank F...   
20  Stormwater runoff from Suncor Plant 2 area (SW...   
21  Stormwater runoff from Suncor Plant 2 area (SW...   

                             Receiving Water                     geometry  
0                     NA (see Outfall 020A)   POINT (-104.94940 39.80500)  
1                     NA (see Outfall 020A)   POINT (-104.94750 39.80720)  
2         

In [6]:
outfalls_gdf.crs

<Geographic 2D CRS: EPSG:4269>
Name: NAD83
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: North America - onshore and offshore: Canada - Alberta; British Columbia; Manitoba; New Brunswick; Newfoundland and Labrador; Northwest Territories; Nova Scotia; Nunavut; Ontario; Prince Edward Island; Quebec; Saskatchewan; Yukon. Puerto Rico. United States (USA) - Alabama; Alaska; Arizona; Arkansas; California; Colorado; Connecticut; Delaware; Florida; Georgia; Hawaii; Idaho; Illinois; Indiana; Iowa; Kansas; Kentucky; Louisiana; Maine; Maryland; Massachusetts; Michigan; Minnesota; Mississippi; Missouri; Montana; Nebraska; Nevada; New Hampshire; New Jersey; New Mexico; New York; North Carolina; North Dakota; Ohio; Oklahoma; Oregon; Pennsylvania; Rhode Island; South Carolina; South Dakota; Tennessee; Texas; Utah; Vermont; Virginia; Washington; West Virginia; Wisconsin; Wyoming. US Virgin Islands. British Virgin Islands

In [7]:
outfalls_z_gdf= gpd.GeoDataFrame(columns=outfalls_gdf.columns)

outfalls_z_gdf

Empty GeoDataFrame
Columns: [Outfall, Description, Latitude, Longitude, Wastewater Source, Receiving Water, geometry]
Index: []

In [8]:
z = []
j = 0

for i in range(len(outfalls_gdf)-1,0,-1):
#    print(i,outfalls_gdf.index[i])
    if('Z' in outfalls_gdf.at[i,'Outfall']):
        z.append(int(i))
        outfalls_z_gdf.loc[j,:] = outfalls_gdf.loc[i,:]
        outfalls_gdf.drop(index=i,axis=0,inplace=True)
        j = j + 1


In [9]:
outfalls_z_gdf

Outfall                                        Description  \
0  028Z (for PFAS)   Retention pond – Plant 2 (southwest corner of ...   
1  027Z (for PFAS)                   Accumulated Stormwater – Plant 2    
2  026Z (for PFAS)   High flow outfall – Plant 3 (at ditch inlet to...   
3  025Z (for PFAS)   High flow outfall – Plant 1 (at sulfur rail lo...   
4  024Z (for PFAS)               Detention area – Plant 2 (north end)    
5  023Z (for PFAS)       Detention area – Plant 1 (west end of swale)    
6  022Z (for PFAS)       Nelson Property pond (northwest corner pond)    
7  021Z (for PFAS)         Nelson Property (northeast corner outfall)    
8  004Z (for PFAS)   Mary’s Pond – Plant 3 (northwest corner outfall)    
9  020Z (for PFAS)   External outfall 020A (at outfall on Sand Creek)    

     Latitude     Longitude  \
0   39.796733   -104.95148    
1   39.801156   -104.94437    
2   39.80376   -104.940982    
3  39.804025   -104.944022    
4  39.804822   -104.942079    
5  39.809017    -104.94901    
6  39.810318   -104.943202    
7  39.810278   -104.940556    
8    39.8075   -104.946667    
9   39.80853     -104.9476    

                                   Wastewater Source  \
0  Stormwater runoff from Suncor Plant 2 area (SW...   
1  Accumulated stormwater runoff from East Tank F...   
2  Stormwater runoff from Suncor Plant 3 commingl...   
3  Stormwater runoff from Suncor Plant 1 (SWA No....   
4  Stormwater runoff from Suncor Plant 2 (SWA No....   
5  Stormwater runoff from Suncor Plant 1 (SWA Nos...   
6  Stormwater runoff from Suncor maintenance faci...   
7  Stormwater runoff from Suncor maintenance faci...   
8  Stormwater runoff from Plant 3 (asphalt plant)...   
9  Combination of treated wastewater from Outfall...   

                            Receiving Water                     geometry  
0  unnamed tributary to South Platte River   POINT (-104.95148 39.79673)  
1         Sand Creek to South Platte River   POINT (-104.94437 39.80116)  
2         Sand Creek to South Platte River   POINT (-104.94098 39.80376)  
3         Sand Creek to South Platte River   POINT (-104.94402 39.80403)  
4         Sand Creek to South Platte River   POINT (-104.94208 39.80482)  
5         Sand Creek to South Platte River   POINT (-104.94901 39.80902)  
6         Sand Creek to South Platte River   POINT (-104.94320 39.81032)  
7         Sand Creek to South Platte River   POINT (-104.94056 39.81028)  
8         Sand Creek to South Platte River   POINT (-104.94667 39.80750)  
9         Sand Creek to South Platte River   POINT (-104.94760 39.80853)

In [10]:
outfalls_gdf.reset_index(inplace=True)

In [11]:
outfalls_gdf

index Outfall                                        Description  \
0       0   002B                               Internal outfall 002    
1       1   003B                               Internal outfall 003    
2       2   020A   External outfall 020A (at outfall on Sand Creek)    
3       4   004A   Mary’s Pond – Plant 3 (northwest corner outfall)    
4       6   021A         Nelson Property (northeast corner outfall)    
5       8   022A       Nelson Property pond (northwest corner pond)    
6      10   023A       Detention area – Plant 1 (west end of swale)    
7      12   024A               Detention area – Plant 2 (north end)    
8      14   025A   High flow outfall – Plant 1 (at sulfur rail lo...   
9      16   026A   High flow outfall – Plant 3 (at ditch inlet to...   
10     18   027A                   Accumulated Stormwater – Plant 2    
11     20   028A   Retention pond – Plant 2 (southwest corner of ...   

      Latitude     Longitude  \
0     39.8050     -104.9494    
1     39.8072     -104.9475    
2    39.80853     -104.9476    
3     39.8075   -104.946667    
4   39.810278   -104.940556    
5   39.810318   -104.943202    
6   39.809017    -104.94901    
7   39.804822   -104.942079    
8   39.804025   -104.944022    
9    39.80376   -104.940982    
10   39.801156   -104.94437    
11   39.796733   -104.95148    

                                    Wastewater Source  \
0   Petroleum refining and related operations, gro...   
1                            Groundwater remediation    
2   Combination of treated wastewater from Outfall...   
3   Stormwater runoff from Plant 3 (asphalt plant)...   
4   Stormwater runoff from Suncor maintenance faci...   
5   Stormwater runoff from Suncor maintenance faci...   
6   Stormwater runoff from Suncor Plant 1 (SWA Nos...   
7   Stormwater runoff from Suncor Plant 2 (SWA No....   
8   Stormwater runoff from Suncor Plant 1 (SWA No....   
9   Stormwater runoff from Suncor Plant 3 commingl...   
10  Accumulated stormwater runoff from East Tank F...   
11  Stormwater runoff from Suncor Plant 2 area (SW...   

                             Receiving Water                     geometry  
0                     NA (see Outfall 020A)   POINT (-104.94940 39.80500)  
1                     NA (see Outfall 020A)   POINT (-104.94750 39.80720)  
2          Sand Creek to South Platte River   POINT (-104.94760 39.80853)  
3          Sand Creek to South Platte River   POINT (-104.94667 39.80750)  
4          Sand Creek to South Platte River   POINT (-104.94056 39.81028)  
5          Sand Creek to South Platte River   POINT (-104.94320 39.81032)  
6          Sand Creek to South Platte River   POINT (-104.94901 39.80902)  
7          Sand Creek to South Platte River   POINT (-104.94208 39.80482)  
8          Sand Creek to South Platte River   POINT (-104.94402 39.80403)  
9          Sand Creek to South Platte River   POINT (-104.94098 39.80376)  
10         Sand Creek to South Platte River   POINT (-104.94437 39.80116)  
11  unnamed tributary to South Platte River   POINT (-104.95148 39.79673)

In [12]:
co_counties_gdf = gpd.read_file('Colorado_County_Boundaries/Colorado_County_Boundaries.shp')

co_counties_gdf.to_crs('EPSG:4269')

OBJECTID       COUNTY                FULL        LABEL CNTY_FIPS  \
0          1      LARIMER      Larimer County      Larimer       069   
1          2   LAS ANIMAS   Las Animas County   Las Animas       071   
2          3      FREMONT      Fremont County      Fremont       043   
3          4     GUNNISON     Gunnison County     Gunnison       051   
4          5      CONEJOS      Conejos County      Conejos       021   
5          6        EAGLE        Eagle County        Eagle       037   
6          7        OTERO        Otero County        Otero       089   
7          8     LA PLATA     La Plata County     La Plata       067   
8          9       SUMMIT       Summit County       Summit       117   
9         10       CUSTER       Custer County       Custer       027   
10        11       PITKIN       Pitkin County       Pitkin       097   
11        12      CROWLEY      Crowley County      Crowley       025   
12        13     CHEYENNE     Cheyenne County     Cheyenne       017   
13        14         BENT         Bent County         Bent       011   
14        15        ADAMS        Adams County        Adams       001   
15        16       ELBERT       Elbert County       Elbert       039   
16        17         YUMA         Yuma County         Yuma       125   
17        18         LAKE         Lake County         Lake       065   
18        19        DELTA        Delta County        Delta       029   
19        20     COSTILLA     Costilla County     Costilla       023   
20        21     GARFIELD     Garfield County     Garfield       045   
21        22       MORGAN       Morgan County       Morgan       087   
22        23      PROWERS      Prowers County      Prowers       099   
23        24    MONTEZUMA    Montezuma County    Montezuma       083   
24        25      MINERAL      Mineral County      Mineral       079   
25        26      LINCOLN      Lincoln County      Lincoln       073   
26        27    JEFFERSON    Jefferson County    Jefferson       059   
27        28   RIO BLANCO   Rio Blanco County   Rio Blanco       103   
28        29     SEDGWICK     Sedgwick County     Sedgwick       115   
29        30   SAN MIGUEL   San Miguel County   San Miguel       113   
30        31      ALAMOSA      Alamosa County      Alamosa       003   
31        32     PHILLIPS     Phillips County     Phillips       095   
32        33        OURAY        Ouray County        Ouray       091   
33        34         MESA         Mesa County         Mesa       077   
34        35     SAGUACHE     Saguache County     Saguache       109   
35        36      DOUGLAS      Douglas County      Douglas       035   
36        37      DOLORES      Dolores County      Dolores       033   
37        38   RIO GRANDE   Rio Grande County   Rio Grande       105   
38        39       PUEBLO       Pueblo County       Pueblo       101   
39        40   KIT CARSON   Kit Carson County   Kit Carson       063   
40        41         BACA         Baca County         Baca       009   
41        42        GRAND        Grand County        Grand       049   
42        43        LOGAN        Logan County        Logan       075   
43        44  CLEAR CREEK  Clear Creek County  Clear Creek       019   
44        45       MOFFAT       Moffat County       Moffat       081   
45        46       TELLER       Teller County       Teller       119   
46        47      BOULDER      Boulder County      Boulder       013   
47        48        KIOWA        Kiowa County        Kiowa       061   
48        49      CHAFFEE      Chaffee County      Chaffee       015   
49        50     HINSDALE     Hinsdale County     Hinsdale       053   
50        51      JACKSON      Jackson County      Jackson       057   
51        52         WELD         Weld County         Weld       123   
52        53     SAN JUAN     San Juan County     San Juan       111   
53        54     MONTROSE     Montrose County     Montrose       085   
54        55   BROOMFIELD   Broomfield Count

In [13]:
#create a b/w map of CONUS
outfall_map = fl.Map(location=[39.8073,-104.9439],
                zoom_start=16,tiles=None)
fl.TileLayer('Stamen Toner',name='BackGround',control=False).add_to(outfall_map)



In [14]:
fl.GeoJson(co_counties_gdf, name='Colorado Counties', control=True,show=False,
               style_function = lambda x: {"weight":1, 
                            'color':'grey',
                            'fillColor':'transparent',
#                            'fillColor':colormap_party(x['properties']['Max']), 
                            'fillOpacity':0.75
               },
           
               highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.25, 
                                'weight': 0.1
               },
 
               tooltip=fl.GeoJsonTooltip(
                   fields=['LABEL'],
                   aliases=['County:'],
                   labels=True,
                   localize=True
              ),
           
              ).add_to(outfall_map)

In [15]:
# Set max zoom level for clusters, also max zoom for spiderfy
zoom_max = 14

# Add Most of the Ponds and Pits to a MarkerCluster layer (clickable)
outfallmarkers = MarkerCluster(name="Outfalls",overlay=True,control=True,disableClusteringAtZoom=zoom_max,
                              spiderfyOnMaxZoom=zoom_max).add_to(outfall_map)

outfalls_gdf.apply(lambda row: 
                        fl.Marker(location=[row['geometry'].y, row['geometry'].x],
                                  icon=DivIcon(
                                      icon_size=(75,15),
#                                      icon_anchor=(-12,12), # shows up on RHS of circle
                                      icon_anchor=(50,12), # shows up on LHS of circle
                                      html='<div style="font-size: 12pt; color:red">%s</div>' % row["Outfall"][0:4],),
                                      tooltip = "Outfall: %s<br>Description %s<br>Wastewater Source: %s<br>Receiving Water%s" % (row['Outfall'],row['Description'],row['Wastewater Source'],row['Receiving Water']) 
                                      ).add_to(outfallmarkers),axis=1)
outfalls_z_gdf.apply(lambda row: 
                        fl.Marker(location=[row['geometry'].y, row['geometry'].x],
                                  icon=DivIcon(
                                      icon_size=(75,15),
                                      icon_anchor=(-12,12), # shows up on RHS of circle
#                                      icon_anchor=(50,12), # shows up on LHS of circle
                                      html='<div style="font-size: 12pt; color:red">%s</div>' % row["Outfall"][0:4],),
                                      tooltip = "Outfall: %s<br>Description %s<br>Wastewater Source: %s<br>Receiving Water%s" % (row['Outfall'],row['Description'],row['Wastewater Source'],row['Receiving Water']) 
                                      ).add_to(outfallmarkers),axis=1)

# Note that CircleMarkers are saved to the MarkerClu0ter layer, not the map
outfalls_gdf.apply(lambda row:
                        fl.CircleMarker(zindexoffset=500,
                                  location=[row['geometry'].y, row['geometry'].x],
                                  max_width=1200,min_width=300,
                                  radius=10,
                                  color='blue',
                                  fill=True,
                                  fill_color='blue',
                                  popup=row['Outfall'],
                            
               highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.75, 
                                'weight': 0.1
               },
               
               tooltip = "Outfall: %s<br>Description %s<br>Wastewater Source: %s<br>Receiving Water%s" % (row['Outfall'],row['Description'],row['Wastewater Source'],row['Receiving Water'])             

                                 ).add_to(outfallmarkers), 
                         axis=1)



0     <folium.vector_layers.CircleMarker object at 0...
1     <folium.vector_layers.CircleMarker object at 0...
2     <folium.vector_layers.CircleMarker object at 0...
3     <folium.vector_layers.CircleMarker object at 0...
4     <folium.vector_layers.CircleMarker object at 0...
5     <folium.vector_layers.CircleMarker object at 0...
6     <folium.vector_layers.CircleMarker object at 0...
7     <folium.vector_layers.CircleMarker object at 0...
8     <folium.vector_layers.CircleMarker object at 0...
9     <folium.vector_layers.CircleMarker object at 0...
10    <folium.vector_layers.CircleMarker object at 0...
11    <folium.vector_layers.CircleMarker object at 0...
dtype: object

In [16]:
# Add minimap
MiniMap(tile_layer='stamenterrain',zoom_level_offset=-5).add_to(outfall_map)

# Finally add control layer and display map
fl.LayerControl(collapsed=False).add_to(outfall_map)

outfall_map

In [17]:
#save the map to an HTML file

if os.path.exists('commercecity_outfalls.html'):
    os.remove('commercecity_outfalls.html')
    
outfall_map.save('commercecity_outfalls.html')